### import

In [35]:
import os
import shutil
import numpy as np
from numpy.linalg import norm
import random
import cv2
import pickle

### defining a siamese model

In [36]:
DATASET_PATH = '../logo_dataset'
BATCH_SIZE = 20

In [48]:
def img_preprocessing(img: np.ndarray):
    img = cv2.resize(img,(400,264))
    if img.shape != (264,400,3):
        raise Exception(f'Shape is not correct : {img.shape}')
    return img 

In [49]:
def create_dataset():
    all_img_ref = []
    all_img_compared = []
    all_label = []
    brand_dir = os.listdir(DATASET_PATH)
    
    for idx_ref, brand in enumerate(os.scandir(DATASET_PATH)):
        if not brand.is_dir:
            pass 
        if idx_ref > 100:
            break
        
        current_img_ref = np.array([]) 
        for idx, file in enumerate(os.scandir(brand.path)): # Img from the same folder
            if idx >= int((BATCH_SIZE/2)) + 1:
                break
            if idx == 0:
                current_img_ref = img_preprocessing(cv2.imread(file.path, cv2.IMREAD_COLOR))
                pass
            try:
                all_img_compared.append(img_preprocessing(cv2.imread(file.path, cv2.IMREAD_COLOR)))
                all_img_ref.append(current_img_ref)
                all_label.append(1)
            except:
                pass
            
        for _ in range(int(BATCH_SIZE/2)):
            r = idx_ref
            while brand_dir[r] == brand.name:
                r = random.randint(0,len(brand_dir)-1)
            brand_compared_name = brand_dir[r]
            brand_compared_dir = os.listdir(os.path.join(DATASET_PATH, brand_compared_name))
            c = random.randint(0,len(brand_compared_dir)-1)
            try:    
                all_img_compared.append(img_preprocessing(cv2.imread(os.path.join(DATASET_PATH, brand_compared_name, brand_compared_dir[c]), cv2.IMREAD_COLOR)))
                all_img_ref.append(current_img_ref)
                all_label.append(0)
            except:
                pass
            
    return all_img_ref, all_img_compared, all_label

In [50]:
df = create_dataset()
print(df)

libpng warning: Unknown iTXt compression type or method


([array([[[255, 255, 255],
        [255, 255, 255],
        [255, 255, 255],
        ...,
        [255, 255, 255],
        [255, 255, 255],
        [255, 255, 255]],

       [[255, 255, 255],
        [255, 255, 255],
        [255, 255, 255],
        ...,
        [255, 255, 255],
        [255, 255, 255],
        [255, 255, 255]],

       [[255, 255, 255],
        [255, 255, 255],
        [255, 255, 255],
        ...,
        [255, 255, 255],
        [255, 255, 255],
        [255, 255, 255]],

       ...,

       [[255, 255, 255],
        [255, 255, 255],
        [255, 255, 255],
        ...,
        [255, 255, 255],
        [255, 255, 255],
        [255, 255, 255]],

       [[255, 255, 255],
        [255, 255, 255],
        [255, 255, 255],
        ...,
        [255, 255, 255],
        [255, 255, 255],
        [255, 255, 255]],

       [[255, 255, 255],
        [255, 255, 255],
        [255, 255, 255],
        ...,
        [255, 255, 255],
        [255, 255, 255],
        [255, 255, 255

In [54]:
fp = open('../utils_/df_object_logo.pickle', 'xb')
pickle.dump(df, fp)

### defining model

In [85]:
from tensorflow.keras.layers import Dense, Flatten, Dropout, MaxPool2D, Conv2D, Input, Layer, Dot
from tensorflow.keras.applications import VGG16, vgg16
from tensorflow.keras import Model, optimizers
import tensorflow as tf
from tensorflow.python.keras.engine import data_adapter
import math
from tensorflow.keras import metrics

In [68]:
with open('../utils_/df_object_logo.pickle', 'rb') as fp:
    df = pickle.load(fp)

In [69]:
X_ref, X_cmp, label = df 

In [98]:
def cosine_similarity(A,B):
    cosine = Dot(axes=0, normalize=True)([A,B])
    return cosine


In [100]:
cosine_similarity(
    np.array([1,1], dtype=np.float64).reshape(-1,1),
    np.array([1,1], dtype=np.float64).reshape(-1,1)
    )


<tf.Tensor: shape=(2, 1), dtype=float32, numpy=
array([[1.],
       [1.]], dtype=float32)>

In [71]:
input = Input((264,400,3), name='img_ref')

preprocessed = vgg16.preprocess_input(input)
encoder = VGG16(include_top=False, input_shape=(264,400,3), input_tensor=preprocessed)

flatten = Flatten()(encoder.output)

embedding = Model(input, flatten, name="Embedding")

for layer in encoder.layers:
    layer.trainable = False


In [72]:
embedding.summary()

Model: "Embedding"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
img_ref (InputLayer)         [(None, 264, 400, 3)]     0         
_________________________________________________________________
tf.__operators__.getitem_9 ( (None, 264, 400, 3)       0         
_________________________________________________________________
tf.nn.bias_add_9 (TFOpLambda (None, 264, 400, 3)       0         
_________________________________________________________________
block1_conv1 (Conv2D)        (None, 264, 400, 64)      1792      
_________________________________________________________________
block1_conv2 (Conv2D)        (None, 264, 400, 64)      36928     
_________________________________________________________________
block1_pool (MaxPooling2D)   (None, 132, 200, 64)      0         
_________________________________________________________________
block2_conv1 (Conv2D)        (None, 132, 200, 128)     73

In [73]:
class DistanceLayer(Layer):
    """
    This layer is responsible for computing the distance between the anchor
    embedding and the positive embedding, and the anchor embedding and the
    negative embedding.
    """

    def __init__(self, **kwargs):
        super().__init__(**kwargs)

    def call(self, anchor, img):
        ap_distance = cosine_similarity(anchor, img)
        return ap_distance

anchor_input = Input(name="anchor", shape=(264,400,3))
img_input = Input(name="img", shape=(264,400,3))

distances = DistanceLayer()(
    embedding(vgg16.preprocess_input(anchor_input)),
    embedding(vgg16.preprocess_input(img_input)),
)

siamese_network = Model(
    inputs=[anchor_input, img_input], outputs=distances
)

In [74]:
cos_input = Input(name="cosine", shape=(1))

dense = Dense(128, activation='relu')(cos_input)
dense_2 = Dense(64, activation='relu')(dense)
dense_3 = Dense(32, activation='relu')(dense_2)
dense_4 = Dense(16, activation='relu')(dense_3)

dense_final = Dense(1, activation='sigmoid')(dense_4)

cosine_network = Model(cos_input, dense_final)

In [79]:
class GlobalModel(Model):
    """The Global Network model with a custom training and testing loops."""
    
    def __init__(self, siamese_network, cosine_network, margin=0.5):
        super(GlobalModel, self).__init__()
        self.siamese_network = siamese_network
        self.cosine_network = cosine_network
        self.margin = margin
        self.loss_tracker = metrics.Mean(name="loss")

    def call(self, inputs):
        #siamese = self.siamese_network(inputs)
        pass
        

    def train_step(self, data):
        data = data_adapter.expand_1d(data)
        x, y, sample_weight = data_adapter.unpack_x_y_sample_weight(data)
        # GradientTape is a context manager that records every operation that
        # you do inside. We are using it here to compute the loss so we can get
        # the gradients and apply them using the optimizer specified in
        # `compile()`.IMREAD_UNCHANGED
        with tf.GradientTape() as tape:
            loss = self._compute_loss(data, y)

        # Storing the gradients of the loss function with respect to the
        # weights/parameters.
        gradients = tape.gradient(loss, self.cosine_network.trainable_weights)

        # Applying the gradients on the model using the specified optimizer
        self.optimizer.apply_gradients(
            zip(gradients, self.cosine_network.trainable_weights)
        )

        # Let's update and return the training loss metric.
        self.loss_tracker.update_state(loss)
        return {"loss": self.loss_tracker.result()}

    def test_step(self, data, y):
        loss = self._compute_loss(data, y)

        # Let's update and return the loss metric.
        self.loss_tracker.update_state(loss)
        return {"loss": self.loss_tracker.result()}

    def _compute_loss(self, data, y):
        cos_distance = self.siamese_network(data)
        print('cos dist :',cos_distance)
        clf_res = self.cosine_network([cos_distance])

        loss = math.sqrt(abs(y-clf_res))
        return loss

    @property
    def metrics(self):
        # We need to list our metrics here so the `reset_states()` can be
        # called automatically.
        return [self.loss_tracker]


In [80]:
global_model = GlobalModel(siamese_network, cosine_network)
global_model.compile(optimizer=optimizers.Adam(0.0001))

In [81]:
X_ref = np.array(X_ref)
X_cmp = np.array(X_cmp)
y = np.array(label)

print(X_ref.shape)
print(X_cmp.shape)
print(y.shape)

(2116, 264, 400, 3)
(2116, 264, 400, 3)
(2116,)


In [101]:
global_model.fit(x=[X_ref,X_cmp], epochs=10)

Epoch 1/10
cos dist : Tensor("model_5/distance_layer_2/dot/Squeeze:0", shape=(None, 1), dtype=float32)


ValueError: in user code:

    /anaconda/lib/python3.9/site-packages/tensorflow/python/keras/engine/training.py:805 train_function  *
        return step_function(self, iterator)
    /anaconda/lib/python3.9/site-packages/tensorflow/python/keras/engine/training.py:795 step_function  **
        outputs = model.distribute_strategy.run(run_step, args=(data,))
    /anaconda/lib/python3.9/site-packages/tensorflow/python/distribute/distribute_lib.py:1259 run
        return self._extended.call_for_each_replica(fn, args=args, kwargs=kwargs)
    /anaconda/lib/python3.9/site-packages/tensorflow/python/distribute/distribute_lib.py:2730 call_for_each_replica
        return self._call_for_each_replica(fn, args, kwargs)
    /anaconda/lib/python3.9/site-packages/tensorflow/python/distribute/distribute_lib.py:3417 _call_for_each_replica
        return fn(*args, **kwargs)
    /anaconda/lib/python3.9/site-packages/tensorflow/python/keras/engine/training.py:788 run_step  **
        outputs = model.train_s